In [2]:
#Plot
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline

#Data Packages
import math
import pandas
import numpy as np
import pandas as pd
#Progress bar
from tqdm import tqdm

#Counter
from collections import Counter

#Operation
import operator

#Natural Language Processing Packages
import re
import nltk

## Download Resources
nltk.download("vader_lexicon")
nltk.download("stopwords")
nltk.download("averaged_perceptron_tagger")
nltk.download("wordnet")

from nltk.sentiment import SentimentAnalyzer
from nltk.sentiment.vader import SentimentIntensityAnalyzer
from nltk.sentiment.util import *
from nltk import tokenize
from nltk.corpus import stopwords
from nltk.tag import PerceptronTagger
from nltk.data import find

## Machine Learning
import sklearn
import sklearn.metrics as metrics

[nltk_data] Downloading package vader_lexicon to
[nltk_data]     C:\Users\Litos\AppData\Roaming\nltk_data...
[nltk_data]   Package vader_lexicon is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\Litos\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     C:\Users\Litos\AppData\Roaming\nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\Litos\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [3]:
# Use vader to evaluated sentiment of reviews
def evalSentences(sentences, to_df=False, columns=[]):
    #Instantiate an instance to access SentimentIntensityAnalyzer class
    sid = SentimentIntensityAnalyzer()
    pdlist = []
    if to_df:
        for sentence in tqdm(sentences):
            ss = sid.polarity_scores(sentence)
            pdlist.append([sentence]+[ss['compound']])
        reviewDf = pandas.DataFrame(pdlist)
        reviewDf.columns = columns
        return reviewDf
    
    else:
        for sentence in tqdm(sentences):
            print(sentence)
            ss = sid.polarity_scores(sentence)
            for k in sorted(ss):
                print('{0}: {1}, '.format(k, ss[k]), end='')
            print()

# Load Data

In [5]:
cur_df = pd.read_csv('../../data/yelp/Data.csv', index_col=0,  encoding='latin-1')

In [6]:
reviews = cur_df['review_text'].values

In [7]:
reviewDF = evalSentences(reviews, to_df=True, columns=['reviewCol','vader'])

100%|█████████████████████████████████████████████████████████████████████████| 169961/169961 [05:04<00:00, 557.57it/s]


In [8]:
reviewDF.head()

reviewCol   vader
0  I ordered the lemon mango slush and the lemon ...  0.9758
1  Came here on a Sunday afternoon, it wasn't bus...  0.9763
2  {Grapefruit & Yakult Green Tea with Aloe Jelly...  0.9170
3  Saw this newly opened bubble tea shop and want...  0.9898
4  Happy Lemon has become my new favourite place ...  0.9922

In [9]:
# #Save
# reviewDF.to_csv('../../data/yelp/reviewDF.csv')

# Find most sentiment words by Mutual Information

## Data preprocessing

In [15]:
# Note: You may want to use an NLTK tokenizer instead of a regular expression in the following
def dataFrameTransformation(cur_df, reviewDF, k=500):
    text = reviewDF['reviewCol'].values
    

#     text = text.replace('.',' ').replace('/t',' ').replace('\t',' ').replace('/',' ').replace('-',' ')
    text = np.char.replace(text, '.',' ')
    
    # Tokenize
#     text = nltk.word_tokenize(reviews)
    # Lowercase
    text = [w.lower() for w in text]
    # Remove Punctuation
    table = str.maketrans('', '', string.punctuation)
    text = [w.translate(table) for w in text]
    # Remove tokens that are not alphabetic
    text = [w for w in text if w.isalpha()]
    
    # Remove Stopwords
    # Get english stopwords
    en_stopwords = set(stopwords.words('english'))
    en_stopwords.remove('off')
    text = [w for w in text if w not in en_stopwords]
    
#     # Lemmatizing
#     lemmatizer = WordNetLemmatizer()
#     text = [lemmatizer.lemmatize(w) for w in text]

#     text = " " + " ".join(str(x) for x in text) + " "

#     text = text.replace('whitish', 'white')
#     text = text.replace('bisquity', ' biscuit ')
#     text = text.replace('carmel', ' caramel ')
#     text = text.replace('flower', ' floral ')
#     text = text.replace('piny', ' pine ')
#     text = text.replace('off white', 'offwhite')
#     text = text.replace('goden', 'gold')
#     text = text.replace('yello', 'yellow')
#     text = text.replace('reddish', ' red ') 
    
#     # Reset to token
#     text = nltk.word_tokenize(text)
#     table = str.maketrans('', '', string.punctuation)
#     text = [w.translate(table) for w in text]
#     text = [w for w in text if w.isalpha()]
# #     en_stopwords = set(stopwords.words('english'))
#     text = [w for w in text if w not in en_stopwords]
    
    # Top-k frequent terms
    counter = Counter()
    reviews = text
    for review in reviews:
            counter.update([word.lower() 
                            for word 
                            in re.findall(r'\w+', review) 
                            if word.lower() not in stop and len(word) > 2])
    topk = counter.most_common(k)        
    
    #Find out if a particular review has the word from topk list
    freqReview = []
    for i in range(len(reviews)):
        tempCounter = Counter([word.lower() for word in re.findall(r'\w+',reviews[i])])
        topkinReview = [1 if tempCounter[word] > 0 else 0 for (word,wordCount) in topk]
        freqReview.append(topkinReview)
        
        
    #Prepare freqReviewDf
    freqReviewDf = pandas.DataFrame(freqReview)
    dfName = []
    for c in topk:
        dfName.append(c[0])
    freqReviewDf.columns = dfName
    finalreviewDf = reviewDF.join(freqReviewDf)
    finaldf = hotelDf[['hotelName','ratingScore','groundTruth']].join(finalreviewDf)
    return topk, finaldf

In [20]:
# Note: You may want to use an NLTK tokenizer instead of a regular expression in the following
def dataFrameTransformation(hotelDf, reviewDF, k=500):
    reviews = reviewDF['reviewCol'].values
    
    stop = set(stopwords.words('english'))
    # Lowercase
    reviews = [w.lower() for w in reviews]
    
    # Top-k frequent terms
    counter = Counter()
    for review in tqdm(reviews):
            counter.update([word.lower() 
                            for word 
                            in re.findall(r'\w+', review) 
                            if word.lower() not in stop and len(word) > 2])
    topk = counter.most_common(k)        
    
    #Find out if a particular review has the word from topk list
    freqReview = []
    for i in tqdm(range(len(reviews))):
        tempCounter = Counter([word.lower() for word in re.findall(r'\w+',reviews[i])])
        topkinReview = [1 if tempCounter[word] > 0 else 0 for (word,wordCount) in topk]
        freqReview.append(topkinReview)
        
        
    #Prepare freqReviewDf
    freqReviewDf = pandas.DataFrame(freqReview)
    dfName = []
    for c in topk:
        dfName.append(c[0])
    freqReviewDf.columns = dfName
    finalreviewDf = reviewDF.join(freqReviewDf)
    finaldf = hotelDf.join(finalreviewDf)
    return topk, finaldf

In [21]:
topk, finaldf = dataFrameTransformation(cur_df, reviewDF, k=500)

100%|████████████████████████████████████████████████████████████████████████| 169961/169961 [00:43<00:00, 3931.70it/s]


ValueError: columns overlap but no suffix specified: Index(['review'], dtype='object')

# Compute Mutual Info

In [22]:
# get Top K mutual information terms from the dataframe
def getMI(topk, df, label_column='groundTruth'):
    miScore = []
    for word in topk:
        miScore.append([word[0]]+[metrics.mutual_info_score(finaldf[label_column], finaldf[word[0]])])
    miScoredf = pandas.DataFrame(miScore).sort_values(1,ascending=0)
    miScoredf.columns = ['Word','MI Score']
    return miScoredf

# Noun Phrase

In [23]:
# Sample text
text = """The Buddha, the Godhead, resides quite as comfortably in the circuits of a digital
computer or the gears of a cycle transmission as he does at the top of a mountain
or in the petals of a flower. To think otherwise is to demean the Buddha...which is
to demean oneself."""

In [24]:
tagger = PerceptronTagger()
# Part of Speech Tagging
# Google: https://en.wikipedia.org/wiki/Part-of-speech_tagging
pos_tag = tagger.tag
taggedToks = pos_tag(re.findall(r'\w+', text))
taggedToks

[('The', 'DT'),
 ('Buddha', 'NNP'),
 ('the', 'DT'),
 ('Godhead', 'NNP'),
 ('resides', 'VBZ'),
 ('quite', 'RB'),
 ('as', 'IN'),
 ('comfortably', 'RB'),
 ('in', 'IN'),
 ('the', 'DT'),
 ('circuits', 'NNS'),
 ('of', 'IN'),
 ('a', 'DT'),
 ('digital', 'JJ'),
 ('computer', 'NN'),
 ('or', 'CC'),
 ('the', 'DT'),
 ('gears', 'NNS'),
 ('of', 'IN'),
 ('a', 'DT'),
 ('cycle', 'NN'),
 ('transmission', 'NN'),
 ('as', 'IN'),
 ('he', 'PRP'),
 ('does', 'VBZ'),
 ('at', 'IN'),
 ('the', 'DT'),
 ('top', 'NN'),
 ('of', 'IN'),
 ('a', 'DT'),
 ('mountain', 'NN'),
 ('or', 'CC'),
 ('in', 'IN'),
 ('the', 'DT'),
 ('petals', 'NNS'),
 ('of', 'IN'),
 ('a', 'DT'),
 ('flower', 'NN'),
 ('To', 'TO'),
 ('think', 'VB'),
 ('otherwise', 'RB'),
 ('is', 'VBZ'),
 ('to', 'TO'),
 ('demean', 'VB'),
 ('the', 'DT'),
 ('Buddha', 'NNP'),
 ('which', 'WDT'),
 ('is', 'VBZ'),
 ('to', 'TO'),
 ('demean', 'VB'),
 ('oneself', 'PRP')]

In [26]:
# This grammar is described in the paper by S. N. Kim,
# T. Baldwin, and M.-Y. Kan.
# Evaluating n-gram based evaluation metrics for automatic
# keyphrase extraction.
# Technical report, University of Melbourne, Melbourne 2010.
grammar = r"""
    NBAR:
        {<NN.*|JJ>*<NN.*>}  # Nouns and Adjectives, terminated with Nouns
        
    NP:
        {<NBAR>}
        {<NBAR><IN><NBAR>}  # Above, connected with in/of/etc...
"""

In [27]:
# Create phrase tree
chunker = nltk.RegexpParser(grammar)
tree= chunker.parse(taggedToks)

In [28]:
# Noun Phrase Extraction Support Functions
from nltk.corpus import stopwords
stopwords = stopwords.words('english')
lemmatizer = nltk.WordNetLemmatizer()
stemmer = nltk.stem.porter.PorterStemmer()

# generator, generate leaves one by one
def leaves(tree):
    """Finds NP (nounphrase) leaf nodes of a chunk tree."""
    for subtree in tree.subtrees(filter = lambda t: t.label()=='NP' or t.label()=='JJ' or t.label()=='RB'):
        yield subtree.leaves()

# stemming, lematizing, lower case... 
def normalise(word):
    """Normalises words to lowercase and stems and lemmatizes it."""
    word = word.lower()
    word = stemmer.stem(word)
    word = lemmatizer.lemmatize(word)
    return word

# stop-words and length control
def acceptable_word(word):
    """Checks conditions for acceptable word: length, stopword."""
    accepted = bool(2 <= len(word) <= 40
        and word.lower() not in stopwords)
    return accepted

# generator, create item once a time
def get_terms(tree):
    for leaf in leaves(tree):
        term = [normalise(w) for w,t in leaf if acceptable_word(w) ]
        # Phrase only
        if len(term)>1:
            yield term

In [29]:
# Traverse tree and get noun phrases
npTokenList = [word for word in get_terms(tree)]

npTokenList

[['digit', 'comput'], ['cycl', 'transmiss']]

In [30]:
# Flatten phrase lists to get tokens for analysis
def flatten(npTokenList):
    finalList =[]
    for phrase in npTokenList:
        token = ''
        for word in phrase:
            token += word + ' '
        finalList.append(token.rstrip())
    return finalList

In [31]:
finalList = flatten(npTokenList)

In [32]:
finalList

['digit comput', 'cycl transmiss']

In [57]:
from ast import literal_eval

# Revise the previous dataframe transform function...
def newDataFrameTransformation(hotelDf, reviewDF, reviewcol_name = 'reviewCol',k= 1000):
    reviews = reviewDF[reviewcol_name].values
    
    
    # Top-k frequent terms
    counter = Counter()
    for review in tqdm(reviews):
            counter.update(flatten([word
                            for word 
                            in get_terms(chunker.parse(pos_tag(re.findall(r'\w+', review)))) 
                            ]))
    topk = counter.most_common(k)        
    
    #Find out if a particular review has the word from topk list
    freqReview = []
    for i in tqdm(range(len(reviews))):
        tempCounter = Counter(flatten([word 
                                       for word 
                                       in get_terms(chunker.parse(pos_tag(re.findall(r'\w+',reviews[i]))))]))
        topkinReview = [1 if tempCounter[word] > 0 else 0 for (word,wordCount) in topk]
        freqReview.append(topkinReview)
         
    #Prepare freqReviewDf
    freqReviewDf = pandas.DataFrame(freqReview)
    dfName = []
    for c in topk:
        dfName.append(c[0])
    freqReviewDf.columns = dfName
    finalreviewDf = reviewDF.join(freqReviewDf)
    finaldf = hotelDf[['business_id','rating','Binary','review','conca_review','UserIndex','ItemIndex']].join(finalreviewDf)
    return topk, finaldf

In [36]:
for i in cur_df:
    print (i)

Unnamed: 0.1
Unnamed: 0.1.1
business_id
friend_count
ghost
img_dsc
img_url
nr
photo_count
rating
review_count
review_date
review_id
review_language
review_text
ufc
user_id
user_loc
vote_count
Updated
Year
Month
Day
Binary
review
conca_review
keyVector
keyphrases_indices_length
UserIndex
ItemIndex


In [58]:
topk_phrase, finaldf_phrase = newDataFrameTransformation(cur_df, reviewDF, k = 1000)



  0%|                                                                                       | 0/169961 [00:00<?, ?it/s]

  0%|                                                                             | 13/169961 [00:00<23:28, 120.69it/s]

  0%|                                                                             | 24/169961 [00:00<24:17, 116.62it/s]

  0%|                                                                             | 40/169961 [00:00<22:36, 125.25it/s]

  0%|                                                                             | 56/169961 [00:00<21:20, 132.74it/s]

  0%|                                                                             | 67/169961 [00:00<24:05, 117.50it/s]

  0%|                                                                             | 79/169961 [00:00<24:08, 117.29it/s]

  0%|                                                                             | 92/169961 [00:00<24:46, 114.25it/s]

  0%|                         

  0%|▎                                                                           | 731/169961 [00:07<27:33, 102.37it/s]

  0%|▎                                                                           | 742/169961 [00:07<27:47, 101.45it/s]

  0%|▎                                                                           | 756/169961 [00:07<25:36, 110.13it/s]

  0%|▎                                                                           | 772/169961 [00:08<23:18, 121.02it/s]

  0%|▎                                                                           | 785/169961 [00:08<27:04, 104.12it/s]

  0%|▎                                                                           | 797/169961 [00:08<27:36, 102.14it/s]

  0%|▎                                                                            | 808/169961 [00:08<28:40, 98.31it/s]

  0%|▎                                                                           | 820/169961 [00:08<28:00, 100.63it/s]

  0%|▍                          

  1%|▋                                                                           | 1543/169961 [00:15<33:52, 82.87it/s]

  1%|▋                                                                           | 1554/169961 [00:15<31:38, 88.68it/s]

  1%|▋                                                                           | 1564/169961 [00:15<30:53, 90.87it/s]

  1%|▋                                                                           | 1574/169961 [00:16<30:26, 92.21it/s]

  1%|▋                                                                           | 1584/169961 [00:16<30:52, 90.89it/s]

  1%|▋                                                                           | 1594/169961 [00:16<33:57, 82.64it/s]

  1%|▋                                                                           | 1605/169961 [00:16<32:00, 87.66it/s]

  1%|▋                                                                           | 1614/169961 [00:16<35:38, 78.71it/s]

  1%|▋                          

  1%|█                                                                           | 2328/169961 [00:23<28:15, 98.87it/s]

  1%|█                                                                          | 2342/169961 [00:23<27:11, 102.77it/s]

  1%|█                                                                          | 2353/169961 [00:23<27:13, 102.58it/s]

  1%|█                                                                          | 2367/169961 [00:23<25:16, 110.54it/s]

  1%|█                                                                          | 2379/169961 [00:24<25:41, 108.69it/s]

  1%|█                                                                          | 2391/169961 [00:24<26:24, 105.74it/s]

  1%|█                                                                          | 2403/169961 [00:24<25:35, 109.13it/s]

  1%|█                                                                          | 2417/169961 [00:24<23:59, 116.37it/s]

  1%|█                          

  2%|█▍                                                                         | 3156/169961 [00:31<23:50, 116.60it/s]

  2%|█▍                                                                         | 3170/169961 [00:31<22:48, 121.89it/s]

  2%|█▍                                                                         | 3184/169961 [00:31<22:01, 126.22it/s]

  2%|█▍                                                                         | 3197/169961 [00:31<26:59, 102.97it/s]

  2%|█▍                                                                          | 3209/169961 [00:32<30:11, 92.06it/s]

  2%|█▍                                                                          | 3222/169961 [00:32<29:26, 94.38it/s]

  2%|█▍                                                                          | 3233/169961 [00:32<31:06, 89.30it/s]

  2%|█▍                                                                          | 3243/169961 [00:32<38:19, 72.50it/s]

  2%|█▍                         

...

 98%|███████████████████████████████████████████████████████████████████████▍ | 166399/169961 [28:59<00:34, 103.37it/s]

 98%|███████████████████████████████████████████████████████████████████████▍ | 166415/169961 [28:59<00:31, 114.23it/s]

 98%|████████████████████████████████████████████████████████████████████████▍ | 166427/169961 [28:59<00:35, 99.58it/s]

 98%|████████████████████████████████████████████████████████████████████████▍ | 166438/169961 [28:59<00:38, 91.35it/s]

 98%|████████████████████████████████████████████████████████████████████████▍ | 166449/169961 [28:59<00:36, 96.06it/s]

 98%|████████████████████████████████████████████████████████████████████████▍ | 166460/169961 [28:59<00:37, 94.54it/s]

 98%|████████████████████████████████████████████████████████████████████████▍ | 166470/169961 [28:59<00:39, 89.49it/s]

 98%|████████████████████████████████████████████████████████████████████████▍ | 166480/169961 [28:59<00:41, 83.26it/s]

 98%|███████████████████████████

 98%|████████████████████████████████████████████████████████████████████████▊ | 167181/169961 [29:07<00:31, 87.56it/s]

 98%|████████████████████████████████████████████████████████████████████████▊ | 167191/169961 [29:07<00:31, 89.32it/s]

 98%|████████████████████████████████████████████████████████████████████████▊ | 167201/169961 [29:07<00:32, 85.27it/s]

 98%|████████████████████████████████████████████████████████████████████████▊ | 167213/169961 [29:07<00:29, 92.79it/s]

 98%|████████████████████████████████████████████████████████████████████████▊ | 167224/169961 [29:07<00:29, 91.38it/s]

 98%|████████████████████████████████████████████████████████████████████████▊ | 167234/169961 [29:07<00:37, 72.81it/s]

 98%|████████████████████████████████████████████████████████████████████████▊ | 167243/169961 [29:07<00:39, 68.18it/s]

 98%|████████████████████████████████████████████████████████████████████████▊ | 167251/169961 [29:08<00:40, 67.60it/s]

 98%|███████████████████████████

 99%|█████████████████████████████████████████████████████████████████████████ | 167948/169961 [29:15<00:22, 87.86it/s]

 99%|█████████████████████████████████████████████████████████████████████████▏| 167958/169961 [29:15<00:23, 84.33it/s]

 99%|█████████████████████████████████████████████████████████████████████████▏| 167969/169961 [29:15<00:22, 88.98it/s]

 99%|█████████████████████████████████████████████████████████████████████████▏| 167979/169961 [29:15<00:21, 91.85it/s]

 99%|█████████████████████████████████████████████████████████████████████████▏| 167989/169961 [29:15<00:24, 79.81it/s]

 99%|█████████████████████████████████████████████████████████████████████████▏| 168003/169961 [29:15<00:21, 90.79it/s]

 99%|█████████████████████████████████████████████████████████████████████████▏| 168013/169961 [29:15<00:22, 86.21it/s]

 99%|█████████████████████████████████████████████████████████████████████████▏| 168026/169961 [29:15<00:20, 93.68it/s]

 99%|███████████████████████████

 99%|█████████████████████████████████████████████████████████████████████████▍| 168690/169961 [29:23<00:14, 84.95it/s]

 99%|█████████████████████████████████████████████████████████████████████████▍| 168703/169961 [29:23<00:13, 93.43it/s]

 99%|█████████████████████████████████████████████████████████████████████████▍| 168716/169961 [29:23<00:13, 94.56it/s]

 99%|████████████████████████████████████████████████████████████████████████▍| 168730/169961 [29:23<00:11, 104.12it/s]

 99%|████████████████████████████████████████████████████████████████████████▍| 168742/169961 [29:23<00:12, 100.87it/s]

 99%|████████████████████████████████████████████████████████████████████████▍| 168753/169961 [29:23<00:11, 101.79it/s]

 99%|█████████████████████████████████████████████████████████████████████████▍| 168764/169961 [29:23<00:12, 95.79it/s]

 99%|█████████████████████████████████████████████████████████████████████████▍| 168774/169961 [29:23<00:13, 90.03it/s]

 99%|███████████████████████████

100%|█████████████████████████████████████████████████████████████████████████▊| 169439/169961 [29:31<00:05, 99.36it/s]

100%|█████████████████████████████████████████████████████████████████████████▊| 169450/169961 [29:31<00:05, 94.50it/s]

100%|█████████████████████████████████████████████████████████████████████████▊| 169461/169961 [29:31<00:05, 96.67it/s]

100%|████████████████████████████████████████████████████████████████████████▊| 169476/169961 [29:31<00:04, 101.28it/s]

100%|████████████████████████████████████████████████████████████████████████▊| 169487/169961 [29:31<00:04, 102.38it/s]

100%|████████████████████████████████████████████████████████████████████████▊| 169498/169961 [29:31<00:04, 103.16it/s]

100%|█████████████████████████████████████████████████████████████████████████▊| 169509/169961 [29:31<00:04, 95.37it/s]

100%|█████████████████████████████████████████████████████████████████████████▊| 169519/169961 [29:31<00:04, 88.82it/s]

100%|███████████████████████████

In [41]:
topk_phrase

[('happi lemon', 4),
 ('milk tea', 4),
 ('cream puff', 4),
 ('first time', 2),
 ('chees drink', 2),
 ('pacif mall', 2),
 ('oreo milk tea', 2),
 ('favourit drink', 2),
 ('bubbletea shop', 1),
 ('intens flavour', 1),
 ('oreo milk tea tast neither', 1),
 ('okay drink lemonadey', 1),
 ('fruitier drink', 1),
 ('salt plum', 1),
 ('mango lemon slushi', 1),
 ('mango matcha latt today', 1),
 ('chewi overal', 1),
 ('daili special', 1),
 ('small tabl', 1),
 ('uniqu drink', 1),
 ('whole store', 1),
 ('salt chees', 1),
 ('happi lemon drink', 1),
 ('bubbl tea', 1),
 ('thick consist', 1),
 ('super cute', 1),
 ('small size', 1),
 ('place servic', 1),
 ('credit card', 1),
 ('next time', 1),
 ('regular medium drink', 1),
 ('first time drink', 1),
 ('mani shop', 1),
 ('order regardless', 1),
 ('chees etc', 1),
 ('bubbl tea shop', 1),
 ('typic normal noth', 1),
 ('medium cup', 1),
 ('memori serv', 1),
 ('bubbl sunday', 1),
 ('salt foam cap', 1),
 ('good imo', 1),
 ('lemon mango slush', 1),
 ('water dow fl

In [43]:
# Compute PMI for all terms and all possible labels
def pmiForAllCal(df, label_column='Binary', topk=topk_phrase):
    #Try calculate all the pmi for top k and store them into one pmidf dataframe
    pmilist = []
    pmiposlist = []
    pmineglist = []
    for word in tqdm(topk):
#         pmilist.append([word[0]]+[pmiCal(df,word[0])])
        pmiposlist.append([word[0]]+[pmiIndivCal(df,word[0],1,label_column)])
        pmineglist.append([word[0]]+[pmiIndivCal(df,word[0],0,label_column)])
    pmidf = pandas.DataFrame(pmilist)
    pmiposlist = pandas.DataFrame(pmiposlist)
    pmineglist = pandas.DataFrame(pmineglist)
    pmiposlist.columns = ['word','pmi']
    pmineglist.columns = ['word','pmi']
#     pmidf.columns = ['word','pmi']
#     return pmiposlist, pmineglist, pmidf
    return pmiposlist, pmineglist

def pmiIndivCal(df,x,gt, label_column='Binary'):
    px = sum(df[label_column]==gt)/len(df)
    py = sum(df[x]==1)/len(df)
    pxy = len(df[(df[label_column]==gt) & (df[x]==1)])/len(df)
    if pxy==0:#Log 0 cannot happen
        pmi = math.log((pxy+0.0001)/(px*py))
    else:
        pmi = math.log(pxy/(px*py))
    return pmi

# Simple example of getting pairwise mutual information of a term
def pmiCal(df, x):
    pmilist=[]
    for i in [1,0]:
        for j in [0,1]:
            px = sum(df['Binary']==i)/len(df)
            py = sum(df[x]==j)/len(df)
            pxy = len(df[(df['Binary']==i) & (df[x]==j)])/len(df)
            if pxy==0:#Log 0 cannot happen
                pmi = math.log((pxy+0.0001)/(px*py))
            else:
                pmi = math.log(pxy/(px*py))
            pmilist.append([i]+[j]+[px]+[py]+[pxy]+[pmi])
    pmidf = pandas.DataFrame(pmilist)
    pmidf.columns = ['x','y','px','py','pxy','pmi']
    return pmidf

In [59]:
pmiposlist, pmineglist = pmiForAllCal(finaldf_phrase, topk=topk_phrase)



  0%|                                                                                         | 0/1000 [00:00<?, ?it/s]

  0%|                                                                                 | 1/1000 [00:02<37:46,  2.27s/it]

  0%|▏                                                                                | 2/1000 [00:03<30:21,  1.82s/it]

  0%|▏                                                                                | 3/1000 [00:03<25:15,  1.52s/it]

  0%|▎                                                                                | 4/1000 [00:04<21:39,  1.30s/it]

  0%|▍                                                                                | 5/1000 [00:05<19:04,  1.15s/it]

  1%|▍                                                                                | 6/1000 [00:06<17:13,  1.04s/it]

  1%|▌                                                                                | 7/1000 [00:07<15:55,  1.04it/s]

  1%|▋                        

  7%|█████▎                                                                          | 67/1000 [00:53<11:51,  1.31it/s]

  7%|█████▍                                                                          | 68/1000 [00:53<11:50,  1.31it/s]

  7%|█████▌                                                                          | 69/1000 [00:54<11:52,  1.31it/s]

  7%|█████▌                                                                          | 70/1000 [00:55<11:55,  1.30it/s]

  7%|█████▋                                                                          | 71/1000 [00:56<11:51,  1.31it/s]

  7%|█████▊                                                                          | 72/1000 [00:56<11:47,  1.31it/s]

  7%|█████▊                                                                          | 73/1000 [00:57<11:46,  1.31it/s]

  7%|█████▉                                                                          | 74/1000 [00:58<11:46,  1.31it/s]

  8%|██████                     

 13%|██████████▌                                                                    | 134/1000 [01:44<11:04,  1.30it/s]

 14%|██████████▋                                                                    | 135/1000 [01:45<11:03,  1.30it/s]

 14%|██████████▋                                                                    | 136/1000 [01:45<11:00,  1.31it/s]

 14%|██████████▊                                                                    | 137/1000 [01:46<10:59,  1.31it/s]

 14%|██████████▉                                                                    | 138/1000 [01:47<10:56,  1.31it/s]

 14%|██████████▉                                                                    | 139/1000 [01:48<10:55,  1.31it/s]

 14%|███████████                                                                    | 140/1000 [01:48<10:56,  1.31it/s]

 14%|███████████▏                                                                   | 141/1000 [01:49<10:54,  1.31it/s]

 14%|███████████▏               

 20%|███████████████▉                                                               | 201/1000 [02:35<10:09,  1.31it/s]

 20%|███████████████▉                                                               | 202/1000 [02:36<10:07,  1.31it/s]

 20%|████████████████                                                               | 203/1000 [02:36<10:07,  1.31it/s]

 20%|████████████████                                                               | 204/1000 [02:37<10:05,  1.31it/s]

 20%|████████████████▏                                                              | 205/1000 [02:38<10:07,  1.31it/s]

 21%|████████████████▎                                                              | 206/1000 [02:39<10:05,  1.31it/s]

 21%|████████████████▎                                                              | 207/1000 [02:39<10:06,  1.31it/s]

 21%|████████████████▍                                                              | 208/1000 [02:40<10:04,  1.31it/s]

 21%|████████████████▌          

 27%|█████████████████████▏                                                         | 268/1000 [03:26<09:17,  1.31it/s]

 27%|█████████████████████▎                                                         | 269/1000 [03:27<09:15,  1.32it/s]

 27%|█████████████████████▎                                                         | 270/1000 [03:27<09:15,  1.31it/s]

 27%|█████████████████████▍                                                         | 271/1000 [03:28<09:13,  1.32it/s]

 27%|█████████████████████▍                                                         | 272/1000 [03:29<09:13,  1.31it/s]

 27%|█████████████████████▌                                                         | 273/1000 [03:30<09:10,  1.32it/s]

 27%|█████████████████████▋                                                         | 274/1000 [03:30<09:12,  1.31it/s]

 28%|█████████████████████▋                                                         | 275/1000 [03:31<09:09,  1.32it/s]

 28%|█████████████████████▊     

...

 67%|████████████████████████████████████████████████████▉                          | 670/1000 [08:30<04:08,  1.33it/s]

 67%|█████████████████████████████████████████████████████                          | 671/1000 [08:31<04:07,  1.33it/s]

 67%|█████████████████████████████████████████████████████                          | 672/1000 [08:31<04:05,  1.34it/s]

 67%|█████████████████████████████████████████████████████▏                         | 673/1000 [08:32<04:04,  1.34it/s]

 67%|█████████████████████████████████████████████████████▏                         | 674/1000 [08:33<04:03,  1.34it/s]

 68%|█████████████████████████████████████████████████████▎                         | 675/1000 [08:34<04:02,  1.34it/s]

 68%|█████████████████████████████████████████████████████▍                         | 676/1000 [08:34<04:02,  1.34it/s]

 68%|█████████████████████████████████████████████████████▍                         | 677/1000 [08:35<04:02,  1.33it/s]

 68%|███████████████████████████

 74%|██████████████████████████████████████████████████████████▏                    | 737/1000 [09:20<03:17,  1.34it/s]

 74%|██████████████████████████████████████████████████████████▎                    | 738/1000 [09:21<03:15,  1.34it/s]

 74%|██████████████████████████████████████████████████████████▍                    | 739/1000 [09:22<03:15,  1.34it/s]

 74%|██████████████████████████████████████████████████████████▍                    | 740/1000 [09:23<03:14,  1.34it/s]

 74%|██████████████████████████████████████████████████████████▌                    | 741/1000 [09:23<03:14,  1.33it/s]

 74%|██████████████████████████████████████████████████████████▌                    | 742/1000 [09:24<03:13,  1.33it/s]

 74%|██████████████████████████████████████████████████████████▋                    | 743/1000 [09:25<03:12,  1.33it/s]

 74%|██████████████████████████████████████████████████████████▊                    | 744/1000 [09:26<03:11,  1.34it/s]

 74%|███████████████████████████

 80%|███████████████████████████████████████████████████████████████▌               | 804/1000 [10:11<02:27,  1.33it/s]

 80%|███████████████████████████████████████████████████████████████▌               | 805/1000 [10:11<02:26,  1.33it/s]

 81%|███████████████████████████████████████████████████████████████▋               | 806/1000 [10:12<02:26,  1.33it/s]

 81%|███████████████████████████████████████████████████████████████▊               | 807/1000 [10:13<02:25,  1.33it/s]

 81%|███████████████████████████████████████████████████████████████▊               | 808/1000 [10:14<02:24,  1.32it/s]

 81%|███████████████████████████████████████████████████████████████▉               | 809/1000 [10:14<02:23,  1.33it/s]

 81%|███████████████████████████████████████████████████████████████▉               | 810/1000 [10:15<02:25,  1.31it/s]

 81%|████████████████████████████████████████████████████████████████               | 811/1000 [10:16<02:24,  1.31it/s]

 81%|███████████████████████████

 87%|████████████████████████████████████████████████████████████████████▊          | 871/1000 [11:01<01:37,  1.33it/s]

 87%|████████████████████████████████████████████████████████████████████▉          | 872/1000 [11:02<01:36,  1.33it/s]

 87%|████████████████████████████████████████████████████████████████████▉          | 873/1000 [11:03<01:36,  1.32it/s]

 87%|█████████████████████████████████████████████████████████████████████          | 874/1000 [11:04<01:35,  1.32it/s]

 88%|█████████████████████████████████████████████████████████████████████▏         | 875/1000 [11:04<01:35,  1.31it/s]

 88%|█████████████████████████████████████████████████████████████████████▏         | 876/1000 [11:05<01:33,  1.32it/s]

 88%|█████████████████████████████████████████████████████████████████████▎         | 877/1000 [11:06<01:33,  1.32it/s]

 88%|█████████████████████████████████████████████████████████████████████▎         | 878/1000 [11:07<01:32,  1.32it/s]

 88%|███████████████████████████

 94%|██████████████████████████████████████████████████████████████████████████     | 938/1000 [11:52<00:46,  1.33it/s]

 94%|██████████████████████████████████████████████████████████████████████████▏    | 939/1000 [11:53<00:46,  1.32it/s]

 94%|██████████████████████████████████████████████████████████████████████████▎    | 940/1000 [11:53<00:45,  1.32it/s]

 94%|██████████████████████████████████████████████████████████████████████████▎    | 941/1000 [11:54<00:44,  1.32it/s]

 94%|██████████████████████████████████████████████████████████████████████████▍    | 942/1000 [11:55<00:44,  1.30it/s]

 94%|██████████████████████████████████████████████████████████████████████████▍    | 943/1000 [11:56<00:43,  1.31it/s]

 94%|██████████████████████████████████████████████████████████████████████████▌    | 944/1000 [11:56<00:42,  1.32it/s]

 94%|██████████████████████████████████████████████████████████████████████████▋    | 945/1000 [11:57<00:41,  1.32it/s]

 95%|███████████████████████████

In [45]:
pmiposlist.sort_values('pmi',ascending=0).head(20)

word       pmi
32                   mani shop  1.609438
33            order regardless  1.609438
12              fruitier drink  1.609438
10  oreo milk tea tast neither  1.609438
18                  small tabl  1.609438
48             real grapefruit  1.609438
5                   pacif mall  0.916291
6                oreo milk tea  0.916291
7               favourit drink  0.916291
1                     milk tea  0.510826
0                  happi lemon  0.510826
38                 memori serv -5.298317
31            first time drink -5.298317
34                   chees etc -5.298317
35              bubbl tea shop -5.298317
36           typic normal noth -5.298317
37                  medium cup -5.298317
41                    good imo -5.298317
39                bubbl sunday -5.298317
40               salt foam cap -5.298317

In [46]:
pmineglist.sort_values('pmi',ascending=0).head(20)

word       pmi
25            super cute  0.223144
37            medium cup  0.223144
26            small size  0.223144
27          place servic  0.223144
28           credit card  0.223144
29             next time  0.223144
30  regular medium drink  0.223144
31      first time drink  0.223144
34             chees etc  0.223144
35        bubbl tea shop  0.223144
36     typic normal noth  0.223144
38           memori serv  0.223144
23             bubbl tea  0.223144
39          bubbl sunday  0.223144
40         salt foam cap  0.223144
41              good imo  0.223144
42     lemon mango slush  0.223144
43     water dow flavour  0.223144
44       bubbl tea place  0.223144
45              gong cha  0.223144

In [60]:
pmineglist.sort_values('pmi',ascending=0).head(20)

word       pmi
328        bad place  0.265478
604        okay noth  0.256685
240     decent place  0.247698
475          ok noth  0.245987
476      decent food  0.241282
983     second chanc  0.240937
954   terribl servic  0.234162
987     mediocr food  0.232658
910    decent servic  0.228065
516      eye contact  0.227738
590          sub par  0.225909
397      slow servic  0.225488
326        high hope  0.224883
463         dri side  0.224458
353        bit bland  0.218122
583       separ bill  0.215995
591       high price  0.215031
410       empti tabl  0.210568
552      poor servic  0.209993
682  room temperatur  0.208400

In [62]:
import pickle as pkl
with open("pmineglist", "wb") as output_file:
    pkl.dump(pmineglist, output_file)
with open("pmiposlist", "wb") as output_file:
    pkl.dump(pmiposlist, output_file)

In [63]:
# topk_phrase, finaldf_phrase
with open("topk_phrase", "wb") as output_file:
    pkl.dump(topk_phrase, output_file)


In [66]:
pmineglist.sort_values('pmi',ascending=0)

word       pmi
328            bad place  0.265478
604            okay noth  0.256685
240         decent place  0.247698
475              ok noth  0.245987
476          decent food  0.241282
983         second chanc  0.240937
954       terribl servic  0.234162
987         mediocr food  0.232658
910        decent servic  0.228065
516          eye contact  0.227738
590              sub par  0.225909
397          slow servic  0.225488
326            high hope  0.224883
463             dri side  0.224458
353            bit bland  0.218122
583           separ bill  0.215995
591           high price  0.215031
410           empti tabl  0.210568
552          poor servic  0.209993
682      room temperatur  0.208400
564          littl bland  0.206675
722            good dish  0.203196
963             bad tast  0.202663
866         averag price  0.200730
889         asian legend  0.200730
520           quick meal  0.194101
659          good overal  0.192602
396           bad servic  0.191825
355           salti side  0.188352
840            high side  0.188224
..                   ...       ...
234         excel servic -0.243886
810          delici meal -0.249810
34          great experi -0.250368
967         awesom place -0.261451
571           super nice -0.265394
130            great job -0.269288
118          delici food -0.271922
804            tast menu -0.274354
64             top notch -0.285093
726        great qualiti -0.302510
537      person favourit -0.305273
834  great custom servic -0.307629
423            real deal -0.318790
962          great coffe -0.321585
904           super help -0.325648
459           escap room -0.345120
779        favourit spot -0.347754
533             much fun -0.360049
799            littl gem -0.364517
109       favourit place -0.369323
450       perfect balanc -0.376326
568             hair cut -0.387435
60            hidden gem -0.399694
655        favorit place -0.420958
930      great recommend -0.435773
724            amaz food -0.445055
884        wonder experi -0.509250
517          amaz servic -0.557090
634     favourit restaur -0.701573
768          amaz experi -0.826423

[1000 rows x 2 columns]

In [67]:
pmiposlist.sort_values('pmi',ascending=0)

word       pmi
768          amaz experi  1.028802
634     favourit restaur  0.959999
517          amaz servic  0.860921
884        wonder experi  0.822245
724            amaz food  0.764650
930      great recommend  0.755719
655        favorit place  0.741120
60            hidden gem  0.719394
568             hair cut  0.706434
450       perfect balanc  0.694402
109       favourit place  0.686673
799            littl gem  0.681301
533             much fun  0.676259
779        favourit spot  0.662131
459           escap room  0.659055
904           super help  0.635759
962          great coffe  0.630772
423            real deal  0.627313
834  great custom servic  0.613286
537      person favourit  0.610280
726        great qualiti  0.606733
64             top notch  0.583849
804            tast menu  0.569270
118          delici food  0.565916
130            great job  0.562260
571           super nice  0.556816
967         awesom place  0.551251
34          great experi  0.535320
810          delici meal  0.534506
234         excel servic  0.525799
..                   ...       ...
840            high side -1.084773
355           salti side -1.086231
396           bad servic -1.126829
659          good overal -1.136162
520           quick meal -1.154436
889         asian legend -1.239882
866         averag price -1.239882
963             bad tast -1.266348
722            good dish -1.273783
564          littl bland -1.323794
682      room temperatur -1.349621
552          poor servic -1.374131
410           empti tabl -1.383136
591           high price -1.456105
583           separ bill -1.472634
353            bit bland -1.510172
463             dri side -1.631670
326            high hope -1.640408
397          slow servic -1.652980
590              sub par -1.661813
516          eye contact -1.701227
910        decent servic -1.708447
987         mediocr food -1.816107
954       terribl servic -1.854135
983         second chanc -2.046973
476          decent food -2.057902
475              ok noth -2.220711
240         decent place -2.287402
604            okay noth -2.740120
328            bad place -3.573029

[1000 rows x 2 columns]